This is to simulate what the solution space of the synthesizing of any product looks like.

In [5]:
import numpy as np
import plotly.graph_objects as go
from data_generation import sigmoid_fn, linear_fn, exp_fn, log_fn, yield_time_x
import pandas as pd
from sklearn.decomposition import PCA

In [2]:
# Parameters
mu = [-6, -1, 9, 4]
tau = 1.8

# Function parameters: (a, b) for sigmoid, linear, exp, log
params = {
    'sigmoid': (0.95, 7, 3),
    'linear': (0.15, 0.1),
    'exp': (0.2, 0.3),
    'log': (0.6, 0)
}

In [3]:
# Create a grid
x_vals = np.linspace(-10, 10, 300)
t_vals = np.linspace(0.01, 5, 300)
X, T = np.meshgrid(x_vals, t_vals)
Z = yield_time_x(X, T, params, tau, mu)
Z[Z < 0] = 0

# Plot with Plotly
fig = go.Figure(data=[go.Surface(z=Z, x=X, y=T, colorscale='Viridis')])
fig.update_layout(
    title='Smooth f(x, t): Sigmoid ↔ Linear ↔ Exp ↔ Log',
    scene=dict(
        xaxis_title='x',
        yaxis_title='t',
        zaxis_title='f(x, t)'
    ),
    autosize=False,
    width=900,
    height=700
)
fig.show()

Formula

$f(x,t)=w_i(x)g_i(t)$

We specify $\tau$ and $\mu_i$ for $i=1,...,n$. We define $Z(x):=\sum_{i=1}^n e^{-(\frac{x-\mu_i}{\tau})^2}$.<p>
$w_i(x):=\frac{e^{-(\frac{x-\mu_i}{\tau})^2}}{Z(x)}$
$g_i(t)$ is either sigmoidal, linear, exponential or logarithmic. Therefore $g_i(t)$ is a sample from the following functions:
- $mt+b$
- $a\ln(t)+v$
- $ce^{\lambda t}$
- $\frac{L}{1+e^{-k(t-p)}}$

Incomplete Example with RAW data excel file

In [35]:
df_time = pd.read_excel('internship_simplified.xlsx',sheet_name='Sheet1')
df_settings = pd.read_excel('internship_simplified.xlsx',sheet_name='Sheet2')

df_settings = df_settings.set_index('well').T.reset_index()
df_settings.columns.name = None
df_settings = df_settings.drop(columns='index')

pca = PCA(n_components=1)
X_pca = pca.fit_transform(X).flatten()

In [56]:
cols= list(df_time.columns)

# Get the time axis in seconds
T = df_time[cols[0]].apply(lambda t: t.hour * 3600 + t.minute * 60 + t.second).to_numpy()

# Z: 2D array, rows = time steps, columns = settings
Z = df_time[cols[2:]].to_numpy()

# X: each column in Z corresponds to a value in df_settings['c1']
X = df_settings['c1'].to_numpy()

In [58]:
np.shape(T),np.shape(X),np.shape(Z)

((93,), (96,), (93, 96))

In [57]:
fig = go.Figure(data=[go.Surface(z=Z, x=X, y=T, colorscale='Viridis')])
fig.update_layout(
    title='Smooth f(x, t): Sigmoid ↔ Linear ↔ Exp ↔ Log',
    scene=dict(
        xaxis_title='x',
        yaxis_title='t',
        zaxis_title='f(x, t)'
    ),
    autosize=False,
    width=900,
    height=700
)
fig.show()